1.豆瓣网排名前250的电影
网址https://movie.douban.com/top250
参考资料来源，有简化和修改
https://blog.csdn.net/wyf2017/article/details/108659289


In [14]:
# 程序参考了网页 
import urllib
import re
import xlwt
from bs4 import BeautifulSoup
from urllib import request
import pandas as pd
import os

def main():
    #https://movie.douban.com/top250?start=25&filter=
    baseUrl = 'https://movie.douban.com/top250?start='
    # 爬取网页
    datalist = getData(baseUrl)
    # 保存数据
    saveData(datalist) 
    askURL(baseUrl)
  
# 创建影片超链接正则表达式
findLink = re.compile(r'<a href="(.*?)">')
# 创建图片正则表达式
findImgSrc = re.compile(r'<img .* src="(.*?)"', re.S)  # re.S的作用是让换行符包含在字符串中
# 创建影片名正则表达式
findTitle = re.compile(r'<span class="title">(.*)</span>')
# 创建评分正则表达式
findRating = re.compile(r'<span class="rating_num" property="v:average">(.*)</span>')
# 创建评价人数正则表达式
findJudge = re.compile(r'<span>(\d*)人评价</span>')
# 创建概况正则表达式
findInq = re.compile(r'<span class="inq">(.*)</span>')
# 创建影片相关内容正则表达式
findBd = re.compile(r'<p class="">(.*?)</p>', re.S)
  
# 爬取网页
def getData(baseUrl):
    datalist = []
    for i in range(0, 6):
        url = baseUrl + str(i*25)
        html = askURL(url)  # 保存获取到的网页
        # 逐一解析数据
        soup = BeautifulSoup(html, 'html.parser')  # 也可以使用lxml代替html.parser作为解析器
        #print(soup.find_all('div', class_="item"))
        # 通过条件筛选我们需要的列表
        for item in soup.find_all('div', class_="item"):
            data = []  # 保存一部电影的所有信息
            item = str(item)  # 将列表转换为字符串
 
            # 获取影片超链接
            link = re.findall(findLink, item)[0]  # re库通过正则表达式来查找指定的字符串
            data.append(link)  # 添加超链接
 
            #  获取图片链接
            imgSrc = re.findall(findImgSrc, item)[0]
            data.append(imgSrc)  # 添加图片链接
 
            # 获取文章标题
            titles = re.findall(findTitle, item)  # 片名可能只有中文名，没有外国名
            if len(titles) == 2:    # 如果有中文和外国名需要分别添加
                ctitle = titles[0]
                data.append(ctitle)  # 添加中文名
                otitle = titles[1].replace("/", " ")   # 去掉标题中的/字符
                data.append(otitle.split())  # 添加英文名,并将空格去掉
            else:
                data.append(titles[0])
                data.append(" ")     # 留空
 
            # 获取影片评分
            rating = re.findall(findRating, item)[0]
            data.append(rating)  # 添加影片评分
 
            # 获取评价人数
            judge = re.findall(findJudge, item)[0]
            data.append(judge)  # 添加评论人数
 
            # 获取概况
            inq = re.findall(findInq, item)
            data.append(inq)  # 添加概况
 
            # 获取影片内容
            bd = re.findall(findBd, item)[0]
            bd = re.sub('<br(\\s+)?/>(\\s+)', " ", bd)  # 使用空格替换掉<br', '>'
            data.append(bd) 
            #data.append(bd.split())  # 去掉前后的空格（\xa0代表空白符&nbsp 使用strip()无法去掉）
            datalist.append(data)   # 将一页的电影信息添加进去
             
    return datalist
 
# 获取网页链接
def askURL(url):
    head = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/74.0.3729.169 Safari/537.36"
    }
    req = urllib.request.Request(url, headers=head)
    html = ""
    try:
        response = urllib.request.urlopen(req)
        html = response.read().decode('utf-8')  # read()获取响应体的内容，内容是bytes字节流，需要转换成字符串
        #print(html)
 
    except urllib.error.URLError as e:
        if hasattr(e,"code"):
            print(e.code)
        if hasattr(e,"reason"):
            print(e.reason)            
    return html
 
# 保存数据
def saveData(datalist):
    # 保存数据
    df=pd.DataFrame(datalist,index=list(range(1,len(datalist)+1)),columns=["movie_weblink", "photo_weblink", "cn_name", "fr_name", "rating", "numbers", "movie_sentence", "movie_details"])
    df.to_csv("D:\\pdata\\python_data\\douban\\movie150.csv",encoding='utf_8_sig') 
    
    # 保存图片(为了提高速度，仅仅保存10部电影的海报)
    for i in range(0,10):
        imgURL = df.iloc[i,1]
        print('保存第%d张电影图片。' % (i+1))
        urllib.request.urlretrieve(imgURL, "D:\\pdata\\python_data\\douban\\top"+str(i+1)+df.iloc[i,2]+".jpg")  
         
if __name__ == '__main__':
    main()
    print("爬取完毕。")

保存第1张电影图片。
保存第2张电影图片。
保存第3张电影图片。
保存第4张电影图片。
保存第5张电影图片。
保存第6张电影图片。
保存第7张电影图片。
保存第8张电影图片。
保存第9张电影图片。
保存第10张电影图片。
爬取完毕。


In [ ]:
# 数据清洗data clean相对繁琐、复杂、耗时较多、未必总能程序操作、可能需要个别手工操作。
#我们跳过这个部分，直接导入已经清晰好的excel格式数据
# 可以从如下网址，下载清洗好的数据
# https://od.lk/d/165582938_pbgd4/movie150clean.xlsx 